#### Create a model with the duplicated regressor

In [19]:
import tensorflow as tf
from dlomix.losses import masked_spectral_distance, masked_pearson_correlation_distance
import keras.backend as K
from dlomix.data import load_processed_dataset
import numpy as np
import os

In [3]:
os.environ["CUDA_VISIBLE_DEVICES"] = "2"

print(f'Number of GPUs available: {len(tf.config.list_physical_devices("GPU"))}')
tf.config.set_soft_device_placement(True)

Number of GPUs available: 1


In [4]:
model = tf.keras.models.load_model("/cmnfs/proj/bmpc_dlomix/models/baseline_models/noptm_baseline_full_bs1024_naivemods/d961f940-d142-4102-9775-c1f8b4373c91.keras")
model.summary()

2024-07-24 07:06:59.509433: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1929] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 7505 MB memory:  -> device: 0, name: NVIDIA GeForce GTX 1080, pci bus id: 0000:81:00.0, compute capability: 6.1


Model: "prosit_intensity_predictor"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       multiple                  432       
                                                                 
 sequential (Sequential)     (None, 30, 512)           1996800   
                                                                 
 sequential_1 (Sequential)   multiple                  4608      
                                                                 
 sequential_2 (Sequential)   (None, 29, 512)           1576806   
                                                                 
 encoder_att (AttentionLaye  multiple                  542       
 r)                                                              
                                                                 
 sequential_3 (Sequential)   multiple                  0         
                                        

In [5]:
dense_weights = model.regressor.get_layer("time_dense").get_weights()[0]
dense_bias = model.regressor.get_layer("time_dense").get_weights()[1]

In [6]:
model.len_fion = 3 * 4
model.regressor = tf.keras.Sequential(
        [
            tf.keras.layers.TimeDistributed(
                tf.keras.layers.Dense(model.len_fion), name='time_dense'
                ), 
            tf.keras.layers.LeakyReLU(name='activation'), 
            tf.keras.layers.Flatten(name='out')], 
        name='regressor'
        )


In [7]:
model.compile(tf.keras.optimizers.Adam(learning_rate=0.0001), loss=masked_spectral_distance)

In [8]:
ds = load_processed_dataset('/cmnfs/proj/bmpc_dlomix/datasets/processed/noptm_baseline_small_duplicated_ions')

In [9]:
ds

DatasetDict({
    train: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 7988
    })
    val: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 3993
    })
    test: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 2000
    })
})

In [10]:
batch, _ = next(iter(ds.tensor_train_data))
model(batch)
model.summary()

2024-07-24 07:07:04.569005: I external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:454] Loaded cuDNN version 8904


Model: "prosit_intensity_predictor"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       multiple                  432       
                                                                 
 sequential (Sequential)     (None, 30, 512)           1996800   
                                                                 
 sequential_1 (Sequential)   multiple                  4608      
                                                                 
 sequential_2 (Sequential)   (None, 29, 512)           1576806   
                                                                 
 encoder_att (AttentionLaye  multiple                  542       
 r)                                                              
                                                                 
 sequential_3 (Sequential)   multiple                  0         
                                        

In [11]:
random_weights = model.regressor.get_layer("time_dense").get_weights()
random_weights

[array([[-0.04743515,  0.03029423,  0.07522633, ...,  0.09796195,
          0.09570932,  0.06531263],
        [ 0.09801248,  0.05920824,  0.09264456, ...,  0.03159594,
         -0.00053206,  0.01585507],
        [-0.03722004, -0.00242648, -0.09839089, ..., -0.01760139,
         -0.01863869, -0.08346559],
        ...,
        [ 0.08121785, -0.04491249, -0.01267993, ...,  0.05562026,
          0.07054079,  0.08436536],
        [-0.05098424, -0.07806063,  0.02166411, ...,  0.08442215,
          0.02581248,  0.03515363],
        [-0.08720721, -0.01531204, -0.06497326, ..., -0.01362327,
         -0.078038  ,  0.02423949]], dtype=float32),
 array([0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.], dtype=float32)]

In [12]:
# set the new weights
model.regressor.get_layer("time_dense").layer.set_weights([K.concatenate([dense_weights, dense_weights], axis=1), K.concatenate([dense_bias, dense_bias], axis=0)])

In [13]:
new_weights = model.regressor.get_layer("time_dense").get_weights()
new_weights

[array([[ 1.2304862e-03, -2.1444494e-03, -3.4535194e-03, ...,
         -1.3421884e-01,  3.0245390e-03,  1.2355821e-03],
        [-1.8715039e-02, -4.2664823e-03,  2.0676129e-03, ...,
          7.9588190e-02, -7.8196189e-04,  4.6518240e-03],
        [-4.9477387e-03, -3.6623156e-01,  6.8261486e-04, ...,
          2.1643376e-03,  2.7091547e-03,  5.6115184e-03],
        ...,
        [ 2.0544356e-01, -5.2947039e-03, -1.2089563e-02, ...,
          3.7856359e-02,  3.3431739e-02,  1.0230787e-02],
        [ 6.4734882e-04, -6.7875260e-03,  6.0291584e-03, ...,
          5.8606756e-03, -5.2891336e-03, -1.7275424e-04],
        [ 4.0923231e-03,  3.7703628e-04, -2.1271440e-03, ...,
         -4.6065997e-02, -1.7431724e-01, -4.0576980e-03]], dtype=float32),
 array([0.05075756, 0.01658243, 0.00654051, 0.01608066, 0.00620176,
        0.00211799, 0.05075756, 0.01658243, 0.00654051, 0.01608066,
        0.00620176, 0.00211799], dtype=float32)]

In [23]:
new_weights[0][0]

array([ 0.00123049, -0.00214445, -0.00345352, -0.13421884,  0.00302454,
        0.00123558,  0.00123049, -0.00214445, -0.00345352, -0.13421884,
        0.00302454,  0.00123558], dtype=float32)

In [14]:
model.summary()

Model: "prosit_intensity_predictor"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       multiple                  432       
                                                                 
 sequential (Sequential)     (None, 30, 512)           1996800   
                                                                 
 sequential_1 (Sequential)   multiple                  4608      
                                                                 
 sequential_2 (Sequential)   (None, 29, 512)           1576806   
                                                                 
 encoder_att (AttentionLaye  multiple                  542       
 r)                                                              
                                                                 
 sequential_3 (Sequential)   multiple                  0         
                                        

In [18]:
model.regressor.get_layer("time_dense").get_weights()[1]

array([0.05075756, 0.01658243, 0.00654051, 0.01608066, 0.00620176,
       0.00211799, 0.05075756, 0.01658243, 0.00654051, 0.01608066,
       0.00620176, 0.00211799], dtype=float32)

In [46]:
res = model.predict(ds.tensor_train_data)

8/8 [==============================] - 1s 74ms/step


In [47]:
res

array([[ 8.9296669e-02, -5.6661834e-04, -4.4695986e-03, ...,
        -2.1391459e-02, -2.2589909e-02,  7.0669544e-01],
       [ 5.0793886e-02,  2.7137101e-03, -2.0164596e-04, ...,
        -8.1389062e-03, -2.9400201e-03,  1.6701178e-01],
       [ 1.0786653e-03, -1.1193680e-03,  5.8291247e-04, ...,
        -2.7921610e-02,  1.9275369e-03,  3.1571513e-01],
       ...,
       [ 2.1322994e-02, -5.3780437e-03, -2.1631394e-03, ...,
        -1.9572521e-02, -1.3189633e-02,  1.1632534e-01],
       [ 2.0532072e-01, -1.8414875e-03, -2.4863195e-03, ...,
        -8.4381782e-02, -9.6328162e-02,  2.0663047e-01],
       [ 3.4747772e-02, -8.1351289e-04, -5.4589368e-04, ...,
        -7.0205233e-03, -2.4078719e-02,  3.2779065e-01]], dtype=float32)

In [48]:
true_vals = ds["train"]["intensities_raw"]
true_vals

[[0.2857142857142857,
  0.0,
  -1.0,
  0.0,
  0.0,
  -1.0,
  0.2857142857142857,
  0.0,
  -1.0,
  0.14285714285714285,
  0.0,
  -1.0,
  0.4285714285714285,
  0.0,
  -1.0,
  1.0,
  0.0,
  -1.0,
  0.35714285714285715,
  0.0,
  -1.0,
  0.4285714285714285,
  0.0,
  -1.0,
  0.21428571428571425,
  0.0,
  -1.0,
  0.5,
  0.0,
  -1.0,
  0.4285714285714285,
  0.0,
  -1.0,
  0.14285714285714285,
  0.0,
  -1.0,
  0.5,
  0.0,
  -1.0,
  0.14285714285714285,
  0.0,
  -1.0,
  0.5714285714285714,
  0.0,
  -1.0,
  0.21428571428571425,
  0.0,
  -1.0,
  0.35714285714285715,
  0.0,
  -1.0,
  0.14285714285714285,
  0.0,
  -1.0,
  0.7142857142857143,
  0.0,
  -1.0,
  0.0,
  0.0,
  -1.0,
  0.7857142857142857,
  0.0,
  -1.0,
  0.14285714285714285,
  0.0,
  -1.0,
  0.6428571428571428,
  0.14285714285714285,
  -1.0,
  0.07142857142857142,
  0.0,
  -1.0,
  0.0,
  0.35714285714285715,
  -1.0,
  0.07142857142857142,
  0.0,
  -1.0,
  0.0,
  0.14285714285714285,
  -1.0,
  0.07142857142857142,
  0.0,
  -1.0,
  -1.0,
 

In [49]:
masked_spectral_distance(np.array(true_vals), res)

<tf.Tensor: shape=(7988,), dtype=float64, numpy=
array([0.66996625, 0.93020569, 0.87431485, ..., 0.94945319, 0.7121025 ,
       0.79551853])>

In [21]:
ds.tensor_val_data

<_PrefetchDataset element_spec=({'modified_sequence': TensorSpec(shape=(None, 30), dtype=tf.int64, name=None), 'precursor_charge_onehot': TensorSpec(shape=(None, 6), dtype=tf.float32, name=None), 'collision_energy_aligned_normed': TensorSpec(shape=(None,), dtype=tf.float32, name=None), 'method_nbr': TensorSpec(shape=(None,), dtype=tf.float32, name=None)}, TensorSpec(shape=(None, 348), dtype=tf.float32, name=None))>

In [16]:
# model.save("/cmnfs/proj/bmpc_dlomix/models/refinement_transfer_learning/double_regressor1.keras")

In [17]:
# new_model = tf.keras.models.load_model("/cmnfs/proj/bmpc_dlomix/models/refinement_transfer_learning/double_regressor1.keras")
# new_model.summary()

### Train the Model

In [18]:
import yaml

In [19]:
config_file_path = '/nfs/home/students/l.willruth/mapra/dlomix/bmpc_shared_scripts/refinement_transfer_learning/config_files/noptm_baseline_small_duplicated_ions_double_regressor.yaml'

with open(config_file_path, 'r') as yaml_file:
    config = yaml.safe_load(yaml_file)

In [20]:
# Initialize wandb
import wandb
from wandb.integration.keras import WandbCallback

project_name = 'duplicated ions tl'
wandb.init(project=project_name,
           config=config,
           entity = 'mapra_dlomix')

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: l1w1 (mapra_dlomix). Use `wandb login --relogin` to force relogin


In [23]:
ds

DatasetDict({
    train: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 7988
    })
    val: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 3993
    })
    test: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 2000
    })
})

In [21]:
model.fit(
    ds.tensor_train_data,
    validation_data=ds.tensor_val_data,
    epochs=config['training']['num_epochs'],
    callbacks=[WandbCallback(save_model=False)]
)

Epoch 1/200


2024-07-23 11:47:28.712312: I external/local_xla/xla/service/service.cc:168] XLA service 0x7fd0649e12d0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2024-07-23 11:47:28.712355: I external/local_xla/xla/service/service.cc:176]   StreamExecutor device (0): NVIDIA GeForce GTX 1080, Compute Capability 6.1
2024-07-23 11:47:28.723124: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:269] disabling MLIR crash reproducer, set env var `MLIR_CRASH_REPRODUCER_DIRECTORY` to enable.
I0000 00:00:1721735248.855214 2150066 device_compiler.h:186] Compiled cluster using XLA!  This line is logged at most once for the lifetime of the process.


8/8 [==============================] - 11s 390ms/step - loss: 0.7483 - val_loss: 0.6744
Epoch 2/200
8/8 [==============================] - 2s 244ms/step - loss: 0.6456 - val_loss: 0.6099
Epoch 3/200
8/8 [==============================] - 2s 248ms/step - loss: 0.5975 - val_loss: 0.5767
Epoch 4/200
8/8 [==============================] - 2s 251ms/step - loss: 0.5694 - val_loss: 0.5541
Epoch 5/200
8/8 [==============================] - 2s 256ms/step - loss: 0.5497 - val_loss: 0.5362
Epoch 6/200
8/8 [==============================] - 2s 252ms/step - loss: 0.5338 - val_loss: 0.5207
Epoch 7/200
8/8 [==============================] - 2s 247ms/step - loss: 0.5194 - val_loss: 0.5076
Epoch 8/200
8/8 [==============================] - 2s 249ms/step - loss: 0.5075 - val_loss: 0.4965
Epoch 9/200
8/8 [==============================] - 2s 247ms/step - loss: 0.4970 - val_loss: 0.4868
Epoch 10/200
8/8 [==============================] - 2s 246ms/step - loss: 0.4880 - val_loss: 0.4787
Epoch 11/200
8/8 [==

In [22]:
ds

DatasetDict({
    train: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 7988
    })
    val: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 3993
    })
    test: Dataset({
        features: ['modified_sequence', 'intensities_raw', 'precursor_charge_onehot', 'collision_energy_aligned_normed', 'method_nbr', '_parsed_sequence', '_n_term_mods', '_c_term_mods'],
        num_rows: 2000
    })
})